In [1]:
import qiskit

In [63]:
from cirq.contrib.qasm_import import circuit_from_qasm
import cirq.contrib.routing as ccr
import cirq
import recirq
import pytket.cirq

def read_qasm_circuit(path):
    qasm_string = open(path, 'r').read()
    try:
        return circuit_from_qasm(qasm_string)
    except:
        print('wrong circuit format')

def get_circuit_depth(circuit):
    return len(cirq.Circuit(circuit.all_operations()))

In [4]:
# 1. scale up rochester
def generate_rochester_style_device(n=1000):
    count = 9
    connection_list = [(0, 1), (1, 2), (2, 3), (3, 4), (4, 5), (5, 6), (6, 7), (7, 8)]
    last_row_indices = [0, 1, 2, 3, 4, 5, 6, 7, 8]
    row_count = 1
    last_index = 8
    while count < n:
        if row_count % 2 == 1:
            if row_count == 1 or row_count % 4 == 3:
                connection_list.append((last_row_indices[0], last_index + 1))
                connection_list.append((last_row_indices[4], last_index + 2))
                connection_list.append((last_row_indices[8], last_index + 3))
                last_row_indices = [last_index + k for k in range(1, 4)]
            else:
                connection_list.append((last_row_indices[2], last_index + 1))
                connection_list.append((last_row_indices[6], last_index + 2))
                connection_list.append((last_row_indices[10], last_index + 3))
                last_row_indices = [last_index + k for k in range(1, 4)]
    
            last_index += 3
        else:
            if count + 9 >= n:
                connection_list.append((last_row_indices[0], last_index + 1))
                connection_list.append((last_row_indices[1], last_index + 5))
                connection_list.append((last_row_indices[2], last_index + 9))
                last_row_indices = [last_index + k for k in range(1, 10)]
                for k in range(1, 9):
                    connection_list.append((last_row_indices[k - 1], last_row_indices[k]))
                last_index += 9
            else:
                if row_count % 4 == 0:
                    connection_list.append((last_row_indices[0], last_index + 1))
                    connection_list.append((last_row_indices[1], last_index + 5))
                    connection_list.append((last_row_indices[2], last_index + 9))
                else:
                    connection_list.append((last_row_indices[0], last_index + 3))
                    connection_list.append((last_row_indices[1], last_index + 7))
                    connection_list.append((last_row_indices[2], last_index + 11))
                    
                last_row_indices = [last_index + k for k in range(1, 12)]
                for k in range(1, 11):
                    connection_list.append((last_row_indices[k - 1], last_row_indices[k]))
                        
                last_index += 11
                
        row_count += 1
        count += len(last_row_indices)
        
    return connection_list

            
            
        

In [32]:
connection_list

[(0, 1),
 (1, 2),
 (2, 3),
 (3, 4),
 (4, 5),
 (5, 6),
 (6, 7),
 (7, 8),
 (0, 9),
 (4, 10),
 (8, 11),
 (9, 12),
 (10, 16),
 (11, 20),
 (12, 13),
 (13, 14),
 (14, 15),
 (15, 16),
 (16, 17),
 (17, 18),
 (18, 19),
 (19, 20)]

In [47]:
connection_list = generate_rochester_style_device()

In [66]:
import pytket
from pytket.circuit import Node
from pytket.predicates import CompilationUnit, ConnectivityPredicate
from pytket.routing import GraphPlacement
from pytket.passes import SequencePass, RoutingPass, DecomposeSwapsToCXs, PlacementPass

def _qubit_index_edges(device):
    index_to_qubit = sorted(device.qubit_set())
    qubit_to_index = {q: i for i, q in enumerate(index_to_qubit)}
    
    dev_graph = ccr.xmon_device_to_graph(device)
    for n1, n2 in dev_graph.edges:
        #yield Node('q', n1.row, n1.col), Node('q', n2.row, n2.col)
        yield (qubit_to_index[n1], qubit_to_index[n2])

def _device_to_tket_device(device):
    arc = pytket.routing.Architecture(
        list(_qubit_index_edges(device))
    )
    print(list(_qubit_index_edges(device)))
    return pytket.device.Device({}, {}, arc)

def _device_connection_list_to_tket_device(device_connection_list):
    arc = pytket.routing.Architecture(device_connection_list)
    return pytket.device.Device({}, {}, arc)

def route_circuit_by_tket(circuit, device_connection_list):
#     index_to_qubit = sorted(device.qubit_set())
#     qubit_to_index = {q: i for i, q in enumerate(index_to_qubit)}
    
    tk_circuit = pytket.cirq.cirq_to_tk(circuit)
    tk_device = _device_connection_list_to_tket_device(device_connection_list)
    print(tk_device)
    
    unit = CompilationUnit(tk_circuit, [ConnectivityPredicate(tk_device)])
#     print(unit.circuit.__repr__())
    passes = SequencePass([
        PlacementPass(GraphPlacement(tk_device)),
        RoutingPass(tk_device, bridge_lookahead=0, bridge_interactions=0)]) # NO BRIDGE
    passes.apply(unit)
    valid = unit.check_all_predicates()
    
    assert valid
    
#     print(unit.circuit.__repr__())
    
    routed_circuit = pytket.cirq.tk_to_cirq(unit.circuit)
#     routed_circuit = routed_circuit.transform_qubits(lambda q: index_to_qubit[q.x])
        
    return routed_circuit

In [49]:
devices = [[(0, 1), (1, 2), (2, 3), (3, 4),
             (0, 5), (4, 6), (5, 9), (6, 13),
             (7, 8), (8, 9), (9, 10), (10, 11), (11, 12), (12, 13), (13, 14), (14, 15),
             (7, 16), (11, 17), (15, 18), (16, 19), (17, 23), (18, 27),
             (19, 20), (20, 21), (21, 22), (22, 23), (23, 24), (24, 25), (25, 26), (26, 27),
             (21, 28), (25, 29), (28, 32), (29, 36),
             (30, 31), (31, 32), (32, 33), (33, 34), (34, 35), (35, 36), (36, 37), (37, 38),
             (30, 39), (34, 40), (38, 41), (39, 42), (40, 46), (41, 50),
             (42, 43), (43, 44), (44, 45), (45, 46), (46, 47), (47, 48), (48, 49), (49, 50),
             (44, 51), (48, 52)]]
for i in range(2, 11):
    devices.append(generate_rochester_style_device(i * 100))

In [ ]:
import time
import os

result = {}
for i, connection_list in enumerate(devices):
    for folder in ['BNTF']:
        for file_str in os.listdir('QUEKO-benchmark/' + folder):
            start_time = time.time()
            best = int(file_str[6:8])
            circuit = read_qasm_circuit('QUEKO-benchmark/'+folder+'/'+file_str)
            routed_circuit = route_circuit_by_tket(circuit, connection_list)
            compiled = get_circuit_depth(routed_circuit)
            key = folder+'/'+device_str
            result[key] = (best, compiled, compiled / best, time.time() - start_time)
#                 print(result[key])
            print(file_str, compiled)
            q16_results[file_str] = [best, compiled, 0]

In [52]:
list(enumerate([1,2,3,4,5]))

[(0, 1), (1, 2), (2, 3), (3, 4), (4, 5)]

In [64]:
%%time
circuit = read_qasm_circuit('QUEKO-benchmark/BSS/53QBT_700CYC_QSE_9.qasm')
routed_circuit = route_circuit_by_tket(circuit, devices[0])
print('depth = ', get_circuit_depth(routed_circuit))

depth =  1806
Wall time: 6.19 s


In [58]:
routed_circuit

┌───┐   ┌──┐   ┌──┐   ┌───┐   ┌───┐   ┌───┐   ┌───┐   ┌───┐   ┌──┐   ┌───┐   ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌───┐   ┌───┐   ┌───┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌───┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐       ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐       ┌──┐   ┌──┐   ┌──┐           ┌──┐       ┌──┐   ┌──┐   ┌──┐   ┌──┐           ┌──┐   ┌──┐   ┌──┐           ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐       ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐       ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐       ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐       ┌──┐       ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐                   ┌──┐   ┌──┐               ┌──┐                       ┌──┐       ┌──┐   ┌──┐   ┌──┐       ┌──┐                   ┌──┐       ┌──┐   ┌──┐               ┌──┐   ┌──┐       ┌──┐       ┌──┐               ┌──┐   ┌──┐   ┌──┐   ┌──┐           ┌───┐               ┌──┐   ┌──┐   ┌──┐                           ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐           ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐       ┌──┐   ┌──┐       ┌──┐   ┌──┐   ┌──┐       ┌───┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐           ┌──┐   ┌──┐   ┌──┐   ┌──┐       ┌──┐   ┌──┐       ┌──┐       ┌──┐   ┌──┐                               ┌──┐   ┌───┐   ┌──┐   ┌───┐   ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐       ┌──┐   ┌──┐   ┌───┐   ┌──┐       ┌──┐   ┌──┐       ┌──┐               ┌──┐               ┌──┐   ┌──┐               ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐       ┌───┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐       ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐       ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐       ┌──┐   ┌──┐   ┌──┐   ┌──┐       ┌──┐   ┌──┐   ┌──┐   ┌───┐       ┌──┐   ┌──┐   ┌──┐                           ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐                       ┌──┐                                   ┌──┐       ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌───┐   ┌──┐       ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌───┐       ┌──┐   ┌──┐       ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐       ┌──┐   ┌──┐   ┌──┐       ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐           ┌──┐                   ┌──┐                               ┌──┐       ┌──┐               ┌──┐   ┌──┐                                                   ┌──┐       ┌───┐   ┌──┐           ┌──┐   ┌──┐           ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐       ┌──┐   ┌──┐       ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐       ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌───┐   ┌───┐   ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐       ┌──┐   ┌──┐       ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐       ┌──┐   ┌──┐   ┌──┐       ┌──┐       ┌──┐           ┌──┐       ┌──┐       ┌──┐   ┌──┐           ┌──┐       ┌──┐       ┌──┐   ┌──┐                       ┌──┐       ┌──┐       ┌──┐                   ┌──┐       ┌──┐   ┌──┐   ┌──┐   ┌──┐           ┌───┐   ┌──┐   ┌──┐   ┌──┐           ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌───┐   ┌──┐   ┌───┐   ┌──┐       ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌───┐   ┌───┐   ┌───┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐   ┌──┐           ┌──┐               ┌──┐       ┌──┐   ┌──┐   ┌──┐   ┌──┐       ┌──┐   ┌──┐       ┌──┐                                               ┌──┐   

In [68]:
routed_circuit2 = route_circuit_by_tket(circuit, devices[1])

<tket::Device>


RuntimeError: Not enough qubits in circuit to make given placement connected

In [71]:
devices[1]

[(0, 1),
 (1, 2),
 (2, 3),
 (3, 4),
 (4, 5),
 (5, 6),
 (6, 7),
 (7, 8),
 (0, 9),
 (4, 10),
 (8, 11),
 (9, 14),
 (10, 18),
 (11, 22),
 (12, 13),
 (13, 14),
 (14, 15),
 (15, 16),
 (16, 17),
 (17, 18),
 (18, 19),
 (19, 20),
 (20, 21),
 (21, 22),
 (12, 23),
 (16, 24),
 (20, 25),
 (23, 26),
 (24, 30),
 (25, 34),
 (26, 27),
 (27, 28),
 (28, 29),
 (29, 30),
 (30, 31),
 (31, 32),
 (32, 33),
 (33, 34),
 (34, 35),
 (35, 36),
 (28, 37),
 (32, 38),
 (36, 39),
 (37, 42),
 (38, 46),
 (39, 50),
 (40, 41),
 (41, 42),
 (42, 43),
 (43, 44),
 (44, 45),
 (45, 46),
 (46, 47),
 (47, 48),
 (48, 49),
 (49, 50),
 (40, 51),
 (44, 52),
 (48, 53),
 (51, 54),
 (52, 58),
 (53, 62),
 (54, 55),
 (55, 56),
 (56, 57),
 (57, 58),
 (58, 59),
 (59, 60),
 (60, 61),
 (61, 62),
 (62, 63),
 (63, 64),
 (56, 65),
 (60, 66),
 (64, 67),
 (65, 70),
 (66, 74),
 (67, 78),
 (68, 69),
 (69, 70),
 (70, 71),
 (71, 72),
 (72, 73),
 (73, 74),
 (74, 75),
 (75, 76),
 (76, 77),
 (77, 78),
 (68, 79),
 (72, 80),
 (76, 81),
 (79, 82),
 (80, 86)

In [ ]:
def 